In [36]:
import numpy as np
import pandas as pd
import os
from tqdm import tqdm
import json

BASE_DIR = "/home/suyash/final_repo/HybridQA_Tab_MM/Hybrid_QA_MM"
# BASE_DIR = "/home/suyash/final_repo/fetaqa_MM_cleaned"
# BASE_DIR = "/home/suyash/final_repo/WikiSQL"
# BASE_DIR = "/home/suyash/final_repo/WikiTableQuestions"

In [37]:
img_pattern = "\{IMG-\{WTQ-\d+-\d+-\d+-\d+-\d+\}\}"
img_overlap_threshold = 1.0
alpha_percent_thresh = 0.5

with open(os.path.join(BASE_DIR, "final_dataset_filtered", "image_id_to_image_path.json"), "r") as f:
    image_id_to_image_path = json.load(f)

with open(os.path.join(BASE_DIR, "final_dataset_filtered", "image_id_to_original_string.json"), "r") as f:
    image_id_to_original_string = json.load(f)


In [38]:
with open(os.path.join(BASE_DIR, "final_dataset_filtered", "questions.jsonl"), "r") as f:
    questions = f.readlines()
    
questions_dict = {}
for question in questions:
    question = json.loads(question)
    questions_dict[question["question_id"]] = question

list(questions_dict.items())[:5]
len(questions_dict)

66148

In [39]:
with open(os.path.join(BASE_DIR, "final_dataset_filtered", "tables.jsonl"), "r") as f:
    tables = f.readlines()
    
tables_dict = {}
for table in tables:
    table = json.loads(table)
    tables_dict[table["table_id"]] = table

list(tables_dict.items())[:5]

[('List_of_mosques_in_Afghanistan_0',
  {'table_id': 'List_of_mosques_in_Afghanistan_0',
   'table_idx': 0,
   'table_array': [['Name', 'Province', 'City', 'Year', 'Remarks'],
    ['abdul rahman mosque',
     'kabul province',
     '{IMG-{HTQ-0-1-2-0}}',
     '2009',
     'Largest mosque in Afghanistan'],
    ['Friday Mosque of Kandahar',
     'kandahar province',
     '{IMG-{HTQ-0-2-2-0}}',
     '1750',
     'Houses the cloak of the Islamic prophet {IMG-{HTQ-0-2-4-0}}'],
    ['Omar Al-Farooq Mosque',
     'Kandahar Province',
     'Kandahar',
     '2014',
     'Built on the site that was a popular cinema of Kandahar . [ 1 ]'],
    ['great mosque of herat',
     'herat province',
     '{IMG-{HTQ-0-4-2-0}}',
     '1446',
     "The mosque was the city 's first congregational mosque , built on the former site of two smaller Zoroastrian Fire temples destroyed by earthquake and fire"],
    ['shrine of ali',
     'balkh province',
     '{IMG-{HTQ-0-5-2-0}}',
     '?',
     'Also known as the

In [40]:
with open(os.path.join(BASE_DIR, "final_dataset_filtered", "image_id_to_original_string.json"), "r") as f:
    image_id_to_original_string = json.load(f)

In [41]:

def clean_string(text):
    return ''.join(char if char.isalnum() else ' ' for char in text)

if BASE_DIR.split("/")[-1] == "WikiSQL":
    TABLE_KEY = "table_id"
else:
    TABLE_KEY = "table_context"
import re

def get_all_image_tags(text):
    pattern = r"\{IMG-\{.*?\}\}"
    matches = re.findall(pattern, text)
    return matches

# for all the questions, get the image_id whose entity is in question 

import re

total_img_ids_counter = 0
set_of_image_strings = set()
question_to_img_ids = {}
missing_tables = 0
set_missing_tables = set()

for question_id, question in questions_dict.items():
    try:
        table = tables_dict[question[TABLE_KEY]]['table_array']
    except:
        # print("Missing table id", question[TABLE_KEY])
        missing_tables += 1
        set_missing_tables.add(question[TABLE_KEY])
        continue
    table_img_id_to_string = {} # img_id -> (og_string, column_header, cell_content, cell_idx_tuple)

    headers = table[0]

    if BASE_DIR.split("/")[-1] == "WikiSQL":
        explicit_cells = question['weak_evidence_idx']
        for row_idx, col_idx in explicit_cells:
            matches = get_all_image_tags(table[row_idx][col_idx])
            for match in matches:
                table_img_id_to_string[match] = (image_id_to_original_string[match], headers[col_idx], table[row_idx][col_idx], tuple([row_idx, col_idx]))
    else:
        for row_idx, row in enumerate(table): 
            for col_idx, cell in enumerate(row): 
                matches = get_all_image_tags(cell)
                total_img_ids_counter += len(matches)
                for match in matches: 
                    try:
                        table_img_id_to_string[match] = (image_id_to_original_string[match], headers[col_idx], cell, tuple([row_idx, col_idx]))
                    except:
                        print("AAAAAAAAAAAAAAA", match)


    #now we need to iterate over all the strings and see if they are in the question
    question_img_ids = []
    cell_content = []
    column_headers = []


    for img_id in table_img_id_to_string: 
        #check percentage of string in question
        cleaned_question = clean_string(question['question'].lower())
        cleaned_img_string = clean_string(table_img_id_to_string[img_id][0].lower())

        question_words = cleaned_question.lower().split()
        img_words = cleaned_img_string.lower().split()
        count = 0
        

        has_useful_token = False

        for word in img_words:
            if word in question_words:
                count += 1
            # alpha_percent = sum(c.isalpha() for c in word)/len(word)
            if len(word)> 2: # and alpha_percent >= alpha_percent_thresh:
                has_useful_token = True

        if not has_useful_token:
            continue
        
        if question_id == "WSQL-77670":
            print(question["question"], table_img_id_to_string[img_id][0], count, question_words, img_words)

        percentage = count/len(img_words)
        if percentage > 0:
            pass

        if percentage >= 1.0:
            question_img_ids.append((img_id, table_img_id_to_string[img_id][0], table_img_id_to_string[img_id][1], table_img_id_to_string[img_id][2], table_img_id_to_string[img_id][3]))
            # print(question["question"], table_img_id_to_string[img_id][0], percentage)
            

        elif percentage >= 0.7:
            pass
            # print(question["question"], table_img_id_to_string[img_id][0], percentage)
            # print(img_words)
        
    
    list_of_img_information = []
    for img_id in question_img_ids:
        list_of_img_information.append({"img_id": img_id[0], "table": question[TABLE_KEY], "img_string": table_img_id_to_string[img_id[0]][0], "cell_string": img_id[3], "column_header": img_id[2], "cell_idx": img_id[4]})
        set_of_image_strings.add(image_id_to_original_string[img_id[0]])
        # print(questions_dict[question]["question"], image_id_to_original_string[img_id],questions_dict[question][TABLE_KEY], img_id) 
    if len(list_of_img_information) > 0:
        question_to_img_ids[question_id] = list_of_img_information

print("Num missing tables", missing_tables)
print(len(questions_dict))
print(len(question_to_img_ids))
print(len(set_missing_tables))

Num missing tables 0
66148
6319
0


In [42]:
question_to_img_ids

{'00009b9649d0dd0a': [{'img_id': '{IMG-{HTQ-0-4-2-0}}',
   'table': 'List_of_mosques_in_Afghanistan_0',
   'img_string': 'herat',
   'cell_string': '{IMG-{HTQ-0-4-2-0}}',
   'column_header': 'City',
   'cell_idx': (4, 2)}],
 '0005a713626c28a0': [{'img_id': '{IMG-{HTQ-6-1-3-0}}',
   'table': '2008_Seattle_Mariners_season_3',
   'img_string': 'university of georgia',
   'cell_string': '{IMG-{HTQ-6-1-3-0}}',
   'column_header': 'School',
   'cell_idx': (1, 3)}],
 '000ceb227f4ebf42': [{'img_id': '{IMG-{HTQ-11-1-3-0}}',
   'table': 'List_of_languages_by_time_of_extinction_26',
   'img_string': 'mesopotamia',
   'cell_string': '{IMG-{HTQ-11-1-3-0}}',
   'column_header': 'Region',
   'cell_idx': (1, 3)},
  {'img_id': '{IMG-{HTQ-11-5-3-2}}',
   'table': 'List_of_languages_by_time_of_extinction_26',
   'img_string': 'mesopotamia',
   'cell_string': 'anatolia ; {IMG-{HTQ-11-5-3-1}} ; {IMG-{HTQ-11-5-3-2}}',
   'column_header': 'Region',
   'cell_idx': (5, 3)}],
 '00192b737629eda1': [{'img_id': '{

In [43]:
with open(os.path.join(BASE_DIR, "final_dataset_filtered", "explicit_questions_data.json"), "w") as f:
    json.dump(question_to_img_ids, f)

In [44]:
len(question_to_img_ids)

6319

In [45]:
for _, arr in list(question_to_img_ids.items())[:100]:
    print("----------------------------")
    og_table_array = tables_dict[questions_dict[_][TABLE_KEY]]["original_table_array"]
    table_context = (arr[0]["table"])
    print(tables_dict[table_context]["table_array"])
    print(tables_dict[table_context]["original_table_array"])
    print(questions_dict[_]['question'])
    print()
    table_array = tables_dict[table_context]["table_array"]
    for elem in arr:
        print(elem['img_string'])
        print(table_array[elem['cell_idx'][0]][elem['cell_idx'][1]])
        print(og_table_array[elem['cell_idx'][0]][elem['cell_idx'][1]])
        print(elem['cell_string'])
    print("----------------------------")

----------------------------
[['Name', 'Province', 'City', 'Year', 'Remarks'], ['abdul rahman mosque', 'kabul province', '{IMG-{HTQ-0-1-2-0}}', '2009', 'Largest mosque in Afghanistan'], ['Friday Mosque of Kandahar', 'kandahar province', '{IMG-{HTQ-0-2-2-0}}', '1750', 'Houses the cloak of the Islamic prophet {IMG-{HTQ-0-2-4-0}}'], ['Omar Al-Farooq Mosque', 'Kandahar Province', 'Kandahar', '2014', 'Built on the site that was a popular cinema of Kandahar . [ 1 ]'], ['great mosque of herat', 'herat province', '{IMG-{HTQ-0-4-2-0}}', '1446', "The mosque was the city 's first congregational mosque , built on the former site of two smaller Zoroastrian Fire temples destroyed by earthquake and fire"], ['shrine of ali', 'balkh province', '{IMG-{HTQ-0-5-2-0}}', '?', 'Also known as the Blue Mosque of Mazar-i-Sharif'], ['sakhi shrine ( Ziarat-e Sakhi )', 'kabul province', '{IMG-{HTQ-0-6-2-0}}', '?', 'Also known as Karte Sakhi Shrine'], ['Mosque of Jalalabad', 'nangarhar province', '{IMG-{HTQ-0-7-2-0

In [46]:
remaining_ques_ids = []
for question in questions_dict:
    if question not in question_to_img_ids:
        remaining_ques_ids.append(question)
print(len(remaining_ques_ids))
print(len(questions_dict))
print(len(question_to_img_ids))

59829
66148
6319


In [47]:
print(remaining_ques_ids[0])

00013190d4370f73


In [48]:
######
# Now explicit mention of entity in answer
# Don't run for FetaQA

if BASE_DIR.split("/")[-1] == "WikiSQL":
    TABLE_KEY = "table_id"
else:
    TABLE_KEY = "table_context"
import re
def get_all_image_tags(text):
    pattern = r"\{IMG-\{.*?\}\}"
    matches = re.findall(pattern, text)
    return matches


# for all the questions, get the image_id whose entity is in question 
import re

total_img_ids_counter = 0
set_of_image_strings = set()
question_to_img_ids = {}
missing_tables = 0

for question_id in remaining_ques_ids:
    question = questions_dict[question_id]
    try:
        table = tables_dict[question[TABLE_KEY]]['table_array']
    except:
        # print("Missing table id", question[TABLE_KEY])
        missing_tables += 1
        continue
    table_img_id_to_string = {} # img_id -> (og_string, column_header, cell_content, cell_idx_tuple)

    headers = table[0]

    if BASE_DIR.split("/")[-1] == "WikiSQL":
        explicit_cells = question['evidence']
        for row_idx, col_idx in explicit_cells:
            matches = get_all_image_tags(table[row_idx][col_idx])
            for match in matches:
                table_img_id_to_string[match] = (image_id_to_original_string[match], headers[col_idx], table[row_idx][col_idx], tuple([row_idx, col_idx]))
    else:
        for row_idx, row in enumerate(table): 
            for col_idx, cell in enumerate(row): 
                matches = get_all_image_tags(cell)
                total_img_ids_counter += len(matches)
                for match in matches: 
                    try:
                        table_img_id_to_string[match] = (image_id_to_original_string[match], headers[col_idx], cell, tuple([row_idx, col_idx]))
                    except:
                        print("AAAAAAAAAAAAAAA", match)


    #now we need to iterate over all the strings and see if they are in the question
    question_img_ids = []
    cell_content = []
    column_headers = []


    for img_id in table_img_id_to_string: 
        #check percentage of string in question
        # if len(question['answer']) > 1:
        #     pass
            # print(question['question'])
            # print(question['answer'])

        if BASE_DIR.split("/")[-1] == "WikiSQL":
            answer_str = " ".join(str(i) for i in question['answer'])
        elif BASE_DIR.split("/")[-1] == "Hybrid_QA_MM":
            answer_str = question['answer-text']
        else:
            answer_str = question['answer']

        cleaned_answer = clean_string(answer_str.lower())
        cleaned_img_string = clean_string(table_img_id_to_string[img_id][0].lower())

        answer_words = cleaned_answer.lower().split()
        img_words = cleaned_img_string.lower().split()
        count = 0
        

        has_useful_token = False

        for word in img_words:
            if word in answer_words:
                count += 1
            # alpha_percent = sum(c.isalpha() for c in word)/len(word)
            if len(word)> 2: # and alpha_percent >= alpha_percent_thresh:
                has_useful_token = True

        if question_id == "WSQL-77670":
            print(question['answer'], table_img_id_to_string[img_id][0], count, img_words, answer_words)
        
        if not has_useful_token:
            continue
        
        percentage = count/len(img_words)
        if percentage > 0:
            pass
        
        if percentage >= img_overlap_threshold:
            question_img_ids.append((img_id, table_img_id_to_string[img_id][0], table_img_id_to_string[img_id][1], table_img_id_to_string[img_id][2], table_img_id_to_string[img_id][3]))
            if question_id == "WSQL-77670":
                print("YASSSSS")
            # print(question["question"], table_img_id_to_string[img_id][0], percentage)
            # print(question["question"], table_img_id_to_string[img_id][0], percentage)
            # print(img_words)
            

        elif percentage >= 0.7:
            pass
        
    
    list_of_img_information = []
    for img_id in question_img_ids:
        list_of_img_information.append({"img_id": img_id[0], "table": question[TABLE_KEY], "img_string": table_img_id_to_string[img_id[0]][0], "cell_string": img_id[3], "column_header": img_id[2], "cell_idx": img_id[4]})
        set_of_image_strings.add(image_id_to_original_string[img_id[0]])
        # print(questions_dict[question]["question"], image_id_to_original_string[img_id],questions_dict[question][TABLE_KEY], img_id) 
    if len(list_of_img_information) > 0:
        question_to_img_ids[question_id] = list_of_img_information

print("Num missing tables", missing_tables)
print(len(tables_dict))
print(len(question_to_img_ids))

# 4,124

Num missing tables 0
12378
5523


In [49]:
with open(os.path.join(BASE_DIR, "final_dataset_filtered", "explicit_answer_mention_data.json"), "w") as f:
    json.dump(question_to_img_ids, f)

In [50]:
print(questions_dict['003770f4fac8aa95']['answer-text'])

Noddy Holder


In [51]:
question_to_img_ids

{'001f6ed558677115': [{'img_id': '{IMG-{HTQ-23-3-1-0}}',
   'table': 'United_States_at_the_2011_World_Aquatics_Championships_0',
   'img_string': 'ryan lochte',
   'cell_string': '{IMG-{HTQ-23-3-1-0}}',
   'column_header': 'Name',
   'cell_idx': (3, 1)},
  {'img_id': '{IMG-{HTQ-23-6-1-0}}',
   'table': 'United_States_at_the_2011_World_Aquatics_Championships_0',
   'img_string': 'ryan lochte',
   'cell_string': '{IMG-{HTQ-23-6-1-0}}',
   'column_header': 'Name',
   'cell_idx': (6, 1)},
  {'img_id': '{IMG-{HTQ-23-8-1-0}}',
   'table': 'United_States_at_the_2011_World_Aquatics_Championships_0',
   'img_string': 'ryan lochte',
   'cell_string': '{IMG-{HTQ-23-8-1-0}}',
   'column_header': 'Name',
   'cell_idx': (8, 1)},
  {'img_id': '{IMG-{HTQ-23-10-1-3}}',
   'table': 'United_States_at_the_2011_World_Aquatics_Championships_0',
   'img_string': 'ryan lochte',
   'cell_string': '{IMG-{HTQ-23-10-1-0}} {IMG-{HTQ-23-10-1-1}} {IMG-{HTQ-23-10-1-2}} {IMG-{HTQ-23-10-1-3}} David Walters {IMG-{HTQ-23

In [52]:
len(question_to_img_ids)

5523

In [53]:
final_qids = []
for question in remaining_ques_ids:
    if question not in question_to_img_ids:
        final_qids.append(question)
print(len(final_qids))
print(len(remaining_ques_ids))
print(len(question_to_img_ids))
remaining_ques_ids = final_qids

54306
59829
5523


In [54]:
for qid, img_ids in question_to_img_ids.items():
    print("----------------------------")
    print("Question: ", questions_dict[qid]['question'])
    if BASE_DIR.split("/")[-1] == "Hybrid_QA_MM":
        print("Answer: ", questions_dict[qid]['answer-text'])
    else:
        print("Answer: ", questions_dict[qid]['answer'])
    for img_id in img_ids:
        print("String corresponding to Img ID:", img_id['img_string'])
        print("Cell string:", img_id['cell_string'])
    print("----------------------------")

----------------------------
Question:  What is the name of the oldest person whose result , not including team race , was above 2 minutes ?
Answer:  Ryan Lochte
String corresponding to Img ID: ryan lochte
Cell string: {IMG-{HTQ-23-3-1-0}}
String corresponding to Img ID: ryan lochte
Cell string: {IMG-{HTQ-23-6-1-0}}
String corresponding to Img ID: ryan lochte
Cell string: {IMG-{HTQ-23-8-1-0}}
String corresponding to Img ID: ryan lochte
Cell string: {IMG-{HTQ-23-10-1-0}} {IMG-{HTQ-23-10-1-1}} {IMG-{HTQ-23-10-1-2}} {IMG-{HTQ-23-10-1-3}} David Walters {IMG-{HTQ-23-10-1-4}}
String corresponding to Img ID: ryan lochte
Cell string: {IMG-{HTQ-23-15-1-0}}
----------------------------
----------------------------
Question:  Who is the recipient whose comments band has sold over 50 million records worldwide ?
Answer:  Noddy Holder
String corresponding to Img ID: noddy holder
Cell string: {IMG-{HTQ-46-3-1-0}}
----------------------------
----------------------------
Question:  What is the call si

In [55]:
def generate_table_string(table_array):
    table_string = ""
    
    for row_idx, row in enumerate(table_array):
        if row_idx == 0:
            # table_string = table_string + "0"
            # for i in range(len(row)):
            #     table_string = table_string + str(i+1) + " | "
            # table_string = table_string + "\n"
            pass
        
        for col_idx, cell in enumerate(row):
            if col_idx == 0:
                pass
                # if row_idx == 0:
                #     pass
                #     table_string = table_string + "index"
                # else:
                #     table_string = table_string + str(row_idx-1)

            cell = cell.replace("\t", " ").replace("\n", " ").replace("\\n", " ").replace("\\t", " ").replace("|", " ")
            table_string = table_string + cell + f" {row_idx, col_idx}" +  " | " 
        table_string = table_string + "\n"
    
    return table_string


In [56]:
qid_to_evidence_cells = {}
if BASE_DIR.split("/")[-1] == "WikiTableQuestions":
    with open("/home/suyash/final_repo/WikiTableQuestions/final_dataset_filtered/qid_to_evidence_cells.json") as f:
        qid_to_evidence_cells = json.load(f)

In [57]:
with open("/home/suyash/final_repo/WTQ_fetching_evidence/qid_to_response.json") as f:
    qid_to_response = json.load(f)
with open("/home/suyash/final_repo/WTQ_fetching_evidence/text_prompts.json") as f:
    qid_to_prompt = json.load(f)

In [58]:
len(remaining_ques_ids)

54306

In [59]:
implicit_only_qids = []
for qid in remaining_ques_ids:
    table_id = questions_dict[qid][TABLE_KEY]
    if table_id not in tables_dict:
        continue
    table_array = tables_dict[table_id]["table_array"]
    if BASE_DIR.split("/")[-1] == "WikiTableQuestions":
        evidence_cells = qid_to_evidence_cells[qid]
    elif BASE_DIR.split("/")[-1] == "WikiSQL":
        evidence_cells = questions_dict[qid]['weak_evidence_idx']
    elif BASE_DIR.split("/")[-1] == "Hybrid_QA_MM":
        evidence_cells = questions_dict[qid]["answer-node"]
        evidence_cells = [tuple([cell[1][0]+1, cell[1][1]]) for cell in evidence_cells]
    else:
        evidence_cells = questions_dict[qid]['highlighted_cell_ids']
    
    for cell in evidence_cells:
        try:
            cell_string = table_array[cell[0]][cell[1]]
        except:
            print("AAAAAAAAAAAAA")
            continue
        if len(get_all_image_tags(cell_string)) > 0:
            implicit_only_qids.append(qid)
            break

print(len(implicit_only_qids))

19581


In [60]:
import random

random.shuffle(implicit_only_qids)

for qid in implicit_only_qids[:20]:
    table_id = questions_dict[qid][TABLE_KEY]
    table_array = tables_dict[table_id]["table_array"]
    table_string = generate_table_string(table_array)
    print("################")
    print(table_string)
    print("-----------------")
    print(qid)
    print(questions_dict[qid]['question'])
    if BASE_DIR.split("/")[-1] == "Hybrid_QA_MM":
        print(questions_dict[qid]['answer-text'])
    else:
        print(questions_dict[qid]['answer'])
    if BASE_DIR.split("/")[-1] == "WikiTableQuestions":
        print(qid_to_prompt[qid])
        print(qid_to_response[qid])
    elif BASE_DIR.split("/")[-1] == "WikiSQL":
        print(questions_dict[qid]['weak_evidence_idx'])
        print(questions_dict[qid]['evidence'])
    elif BASE_DIR.split("/")[-1] == "Hybrid_QA_MM":
        evidence_cells = questions_dict[qid]["answer-node"]
        evidence_cells = [tuple([cell[1][0]+1, cell[1][1]]) for cell in evidence_cells]
        print(evidence_cells)
    else:
        print(questions_dict[qid]['highlighted_cell_ids'])
    print("------------------")
    print("###############")
    

################
State (0, 0) | Location (0, 1) | Area (0, 2) | Character (0, 3) | 
{IMG-{HTQ-7704-1-0-0}} (1, 0) | halibut cove (1, 1) | entire Town (1, 2) | Originally a fishing village , Halibut Cove , located inside Kachemak Bay State Park , is now home to several art studios/galleries and businesses . One of the world 's only floating towns , it is a popular tourist destination . Only way to get around the cove is by boat . Outside access is by water taxis from Homer , 6 miles away (1, 3) | 
{IMG-{HTQ-7704-2-0-0}} (2, 0) | arcosanti (2, 1) | entire town (2, 2) | Arcology being built by {IMG-{HTQ-7704-2-3-0}} (2, 3) | 
{IMG-{HTQ-7704-3-0-0}} (3, 0) | phantom ranch (3, 1) | entire village (3, 2) | Tourist village on the Colorado River inside {IMG-{HTQ-7704-3-3-0}} ten miles ( plus one vertical mile ) from nearest road with access by foot , raft , or mule (3, 3) | 
{IMG-{HTQ-7704-4-0-0}} (4, 0) | Supai , Arizona (4, 1) | entire town (4, 2) | In the havasupai Nation , the capital of S

In [61]:
# from pprint import pprint

# implicit_question_ids = []

# for ques_id in final_qids:
#     table_id = questions_dict[ques_id]["table_context"]
#     if BASE_DIR.split("/")[-1] == "WikiSQL":
#         highlighted_cells = questions_dict[ques_id]['weak_evidence_idx']
#     elif BASE_DIR.split("/")[-1] == "Hybrid_QA_MM":
#         highlighted_cells = questions_dict[ques_id]["answer-node"]
#         highlighted_cells = [tuple([cell[1][0]+1, cell[1][1]]) for cell in highlighted_cells]
#         print(highlighted_cells)
#     else:    
#         highlighted_cells = questions_dict[ques_id]["highlighted_cell_ids"]
    
    
#     if table_id not in tables_dict:
#         continue
    
#     table_array = tables_dict[table_id]['table_array']
#     og_table_array = tables_dict[table_id]['original_table_array']
    
#     for cell in highlighted_cells:
#         if get_all_image_tags(table_array[cell[0]][cell[1]]):
#             implicit_question_ids.append(ques_id)
#             break

In [62]:

print(len(implicit_only_qids))

19581


In [63]:
with open(os.path.join(BASE_DIR, "final_dataset_filtered", "implicit_questions_data.json"), "w") as f:
    json.dump(implicit_only_qids, f)

In [64]:
# PROMPT_TEMPLATE = """You are given a table, alongside a question based on the table and its answer, your task is to identify and report the specific cells within the table that directly provide the answer or were indirectly used to derive the answer. This task may require you to examine each cell attentively, as the necessary evidence could be found across various rows and columns. The identification process might involve mathematical calculations (such as addition, subtraction, or counting) or logical deductions based on information spread across multiple table entries. Each row in the table is given in a new line, and different columns are separated by a tab space. Indices of the rows and columns are also specified to aid in answering the query.
# The reason should include the cell indices of every reference, even name-lookup from the table of entities in the question and the entity in the final answer. If the evidence is spread across multiple rows or columns, ensure all relevant cells are listed. If no relevant evidence can be located within the table to support the answer, you should respond with 'None'. If the final answer is inferred from a cell, that cell's indices should also be included in the evidence. Thus, the evidence cells are union of question cells, final answer cells and all the cells used for reasoning to get to the answer cell(s) from the question cell(s).

# Your response should format the evidence as follows: "Evidence cells: (Row1, Column1), (Row2, Column2), (Row3, Column3)", adjusting as needed for multiple entries. 

# IMPORTANT: To identify the evidence cells, you must follow the following steps:
# Step 1: Carefully analyze the table, the question and the answer provided and write a detailed reason behind getting the answer given the question. Make it as explicit as possible, and include all the entities from the table which were used to derive the answer or were directly used to provide the answer. Here, entity includes anything mentioned in a table cell, whether it is a concept, a piece of information, or an actual entity. IMPORTANT: YOU MUST MAKE THIS AS EXPLICIT AND DETAILED AS POSSIBLE, MENTIONING NOT JUST THE APPROACH BUT WHAT OPERATIONS WERE PERFORMED ON WHAT CELLS TO REACH THE ANSWER.
# Step 2: From the question, answer, reason and the table, list out all the references from the table in the reason, question and answer, along with their respective cell locations. Ensure that any piece of text in the reason, the question and the answer that is also present in the table is included here with the cell location. IMPORTANT: Any information that is used in the reason, question or the answer that is present in the table should be included here. DO NOT LEAVE ANY INFORMATION. IMPORTANT: YOU MUST LIST EACH REFERENCE EXPLICITLY AND MENTION THE CELL LOCATION.
# Step 3: List out all the references to the cells of the table that were mentioned in the question. IMPORTANT: YOU MUST LIST EACH REFERENCE EXPLICITLY AND MENTION THE CELL LOCATION.
# Step 4: List out all the references to the cells of the table that were mentioned in the answer. IMPORTANT: YOU MUST LIST EACH REFERENCE EXPLICITLY AND MENTION THE CELL LOCATION.
# Step 5: Based on the cell references identified in step 2, 3 and 4, list out all the cells from the table which were used to derive the answer or were directly used to provide the answer. Ensure that all the cell references from step 2, 3 and 4 are included here.

# Here are a few examples, with index columns added separately for clarity in the table (and not counted in the cell indices):

# Example 1
# Table:  
#     0                   1         2      3
# index  Team                County    Wins   Years won 
# 0  Greystones          Wicklow       1        2011
# 1  Ballymore Eustace   Kildare       1        2010
# 2  Maynooth            Kildare       1        2009
# 3  Ballyroan Abbey     Laois         1        2008
# 4  Fingal Ravens       Dublin        1        2007
# 5  Confey              Kildare       1        2006
# 6  Crettyard           Laois         1        2005
# 7  Wolfe Tones         Meath         1        2004
# 8  Dundalk Gaels       Louth         1        2003

# Question: which team won previous to crettyard?
# Answer: Wolfe Tones
# Step 1 Reason: crettyard (identified from cell (6,0)) won in 2005 (identified from cell (6,4)), so the previous team would have won in 2004 (identified from cell (7,4)) which is Wolfe Tones (identified from cell (7,0)).
# Step 2 Entities referenced from table with cells: crettyard (6,0), 2005 (6,4), 2004 (7,4), Wolfe Tones (7,0)
# Step 3 Entities referenced from table in the question: crettyard (6,0)
# Step 4 Entities referenced from table in the answer: Wolfe Tones (7,0)
# Step 5 Evidence cells: (6,0), (6,4), (7,4), (7,0)

# Example 2
# Table: 
#     0      1                            2            3         4
# index  Rank   City                         Passengers   Ranking   Airline              
# 0      1  United States, Los Angeles   14,749                 Alaska Airlines      
# 1      2  United States, Houston       5,465                  United Express       
# 2      3  Canada, Calgary              3,761                  Air Transat, WestJet 
# 3      4  Canada, Saskatoon            2,282        4                              
# 4      5  Canada, Vancouver            2,103                  Air Transat          
# 5      6  United States, Phoenix       1,829        1         US Airways  
# 6      7  Canada, Toronto              1,202        1         Air Transat, CanJet
# 7      8  Canada, Edmonton             110                                         
# 8      9  United States, Oakland       107                             
# Question: how many more passengers flew to los angeles than to saskatoon from manzanillo airport in 2013?
# Answer: 12,467
# Step 1 Reason: The number of passengers corresponding to Los Angeles (identified from cell (0,1)) is 14,749 (identified from the cell (0,2)), and the number of passengers corresponding to Saskatoon (identified from cell (3,1)) is 2,282 (identified from the cell (3,2)). The difference between these two values is 12,467.
# Step 2 Entities referenced from table with cells: Los Angeles (0,1), 14,749 (0,2), Saskatoon (3,1), 2,282 (3,2)
# Step 3 Entities referenced from table in the question: Los Angeles (0,1), Saskatoon (3,1)
# Step 4 Entities referenced from table in the answer: None
# Step 5 Evidence: (0,1), (0,2), (3,1), (3,2)

# Example 3
# Table:
#     0      1          2                     3                4                 5                 6
# index  Year   Division   League                Regular Season   Playoffs          Open Cup          Avg. Attendance
# 0   2001          2  USL A-League          4th, Western     Quarterfinals     Did not qualify   7,169 
# 1   2002          2  USL A-League          2nd, Pacific     1st Round         Did not qualify   6,260
# 2   2003          2  USL A-League          3rd, Pacific     Did not qualify   Did not qualify   5,871
# 3   2004          2  USL A-League          1st, Western     Quarterfinals     4th Round         5,628
# 4   2005          2  USL First Division    5th              Quarterfinals     4th Round         6,028
# 5   2006          2  USL First Division    11th             Did not qualify   3rd Round         5,575
# 6   2007          2  USL First Division    2nd              Semifinals        2nd Round         6,851
# 7   2008          2  USL First Division    11th             Did not qualify   1st Round         8,567
# 8   2009          2  USL First Division    1st              Semifinals        3rd Round         9,734
# 9   2010          2  USSF D-2 Pro League   3rd, USL (3rd)   Quarterfinals     3rd Round         10,727
# Question: what was the last year where this team was a part of the usl a-league?
# Answer : 2004
# Step 1 Reason: The years when this team was a part of the USL A-League (identified from the cells (0,2), (1,2), (2,2), (3,2)) was in the years 2001 (identfied from the cell (0,0)), 2002 (identified from the cell (1,0)), 2003 (identified from the cell (2,0)), and 2004 (identified from the cell (3,0)). Thus, the last year when this team was a part of the USL A-League was 2004.
# Step 2 Entities referenced from table with cells: USL A-League (0,2), USL A-League (1,2), USL A-League (2,2), USL A-League (3,2), 2001 (0,0), 2002 (1,0), 2003 (2,0), 2004 (3,0)
# Step 3 Entities referenced from table in the question: USL A-League (0,2), USL A-League (1,2), USL A-League (2,2), USL A-League (3,2)
# Step 4 Entities referenced from table in the answer: 2004 (3,0)
# Step 5 Evidence: (0,2), (0,0), (1,2), (1,0), (2,2), (2,0), (3,2), (3,0)

# Example 4
# Table:
#     0    1                    2                   3                4                       5
# index       Name                 Took office         Left office      Party                   Notes/Events                                                      
# 0   11  William McCreery     March 4, 1803       March 3, 1809    Democratic Republican                                                                     
# 1   12  Alexander McKim      March 4, 1809       March 3, 1815    Democratic Republican                                                                     
# 2   13  William Pinkney      March 4, 1815       April 18, 1816   Democratic Republican   Resigned to accept position as Minister Plenipotentiary to Russia 
# 3   14  Peter Little         September 2, 1816   March 3, 1823    Democratic Republican                                                                     
# 4   14  Peter Little         March 4, 1823       March 3, 1825    Jacksonian DR                                                                             
# 5   14  Peter Little         March 4, 1825       March 3, 1829    Adams                                                                                     
# 6   15  Benjamin C. Howard   March 4, 1829       March 3, 1833    Jacksonian   
# Question : how many people stayed at least 3 years in office?
# Answer : 4
# Step 1 Reason: Take the difference between all the cells March 4, 1803 (0, 2), March 3, 1809 (0,3) & March 4 1809 (1,2), March 3, 1815 (1,3) & March 4, 1815 (2,2), April 18, 1816 (2,3) & September 2, 1816 (3,2), March 3, 1823 (3,3) &  March 4, 1823 (4,2), March 3, 1825 (4,3) & March 4, 1825 (5,2), March 3, 1829 (5,3) & March 4, 1829 (6,2), March 3, 1833 (6,3) and count the number of differences greater than 3. We will find only the difference in the rows 0, 1, 5 and 6 is greater than 3. Thus, the answer is 4.
# Step 2 Entities referenced from the table with cells: March 4, 1803 (0, 2), March 3, 1809 (0,3), March 4 1809 (1,2), March 3, 1815 (1,3), March 4, 1815 (2,2), April 18, 1816 (2,3), September 2, 1816 (3,2), March 3, 1823 (3,3), March 4, 1823 (4,2), March 3, 1825 (4,3), March 4, 1825 (5,2), March 3, 1829 (5,3), March 4, 1829 (6,2), March 3, 1833 (6,3)
# Step 3 Entities referenced from table in the question: None
# Step 4 Entities referenced from table in the answer: None
# Step 5 Evidence : (0,2), (0,3), (1,2), (1,3), (2,2), (2,3), (3,2), (3,3), (4,2), (4,3) (5,2), (5,3), (6,2), (6,3)

# Now, given the table, question and answer, you need to identify the evidence cells while following step 1, step 2 and step 3. Do not include extra information. You must follow the following steps as illustrated above. IMPORTANT: FOLLOW THE DETAIL AND THE PATTERN FOR EACH STEP THAT HAS BEEN DESCRIBED ABOVE.

# Table:
# {table_string}
# Question: {question}
# Answer: {answer}
# Step 1 Reason: """

In [65]:
def generate_table_string(table_array):
    table_string = ""
    
    for row_idx, row in enumerate(table_array):
        if row_idx == 0:
            table_string = table_string + "0"
            for i in range(len(row)):
                table_string = table_string + " | " + str(i+1)
            table_string = table_string + "\n"
        
        for col_idx, cell in enumerate(row):
            if col_idx == 0:
                if row_idx == 0:
                    table_string = table_string + "index"
                else:
                    table_string = table_string + str(row_idx-1)

            cell = cell.replace("\t", " ").replace("\n", " ").replace("\\n", " ").replace("\\t", " ").replace("|", " ")
            table_string = table_string + " | " + cell
        table_string = table_string + "\n"
    
    return table_string

EXAMPLE_1 = {
    "table_array": [["Team", "County", "Wins", "Years won"], ["Greystones", "Wicklow", "1", "2011"], ["Ballymore Eustace", "Kildare", "1", "2010"], ["Maynooth", "Kildare", "1", "2009"], ["Ballyroan Abbey", "Laois", "1", "2008"], ["Fingal Ravens", "Dublin", "1", "2007"], ["Confey", "Kildare", "1", "2006"], ["Crettyard", "Laois", "1", "2005"], ["Wolfe Tones", "Meath", "1", "2004"], ["Dundalk Gaels", "Louth", "1", "2003"]],
    "question": "which team won previous to crettyard?",
    "answer": "Wolfe Tones",
    "step_1": "crettyard (identified from cell (6,1)) won in 2005 (identified from cell (6,4)), so the previous team would have won in 2004 (identified from cell (7,4)) which is Wolfe Tones (identified from cell (7,1)).",
    "step_2": "crettyard (6,1), 2005 (6,4), 2004 (7,4), Wolfe Tones (7,1)",
    "step_3": "crettyard (6,1)",
    "step_4": "Wolfe Tones (7,1)",
    "step_5": "(6,1), (6,4), (7,3), (7,1)"
}

EXAMPLE_2 = {
    "table_array": [["Rank", "City", "Passengers", "Ranking", "Airline"], ["1", "United States, Los Angeles", "14,749", "", "Alaska Airlines"], ["2", "United States, Houston", "5,465", "", "United Express"], ["3", "Canada, Calgary", "3,761", "", "Air Transat, WestJet"], ["4", "Canada, Saskatoon", "2,282", "4", ""], ["5", "Canada, Vancouver", "2,103", "", "Air Transat"], ["6", "United States, Phoenix", "1,829", "1", "US Airways"], ["7", "Canada, Toronto", "1,202", "1", "Air Transat, CanJet"], ["8", "Canada, Edmonton", "110", "", ""], ["9", "United States, Oakland", "107", "", ""]],
    "question": "how many more passengers flew to los angeles than to saskatoon from manzanillo airport in 2013?",
    "answer": "12,467",
    "step_1": "The number of passengers corresponding to Los Angeles (identified from cell (0,2)) is 14,749 (identified from the cell (0,3)), and the number of passengers corresponding to Saskatoon (identified from cell (3,2)) is 2,282 (identified from the cell (3,3)). The difference between these two values is 12,467.",
    "step_2": "Los Angeles (0,2), 14,749 (0,3), Saskatoon (3,2), 2,282 (3,3)",
    "step_3": "Los Angeles (0,2), Saskatoon (3,2)",
    "step_4": "None",
    "step_5": "(0,2), (0,3), (3,2), (3,3)"
}

EXAMPLE_3 = {
    "table_array": [['Year', 'Competition', 'Venue', 'Position', 'Event', 'Notes'], ['2002', 'Central American and Caribbean Junior Championships (U-17)', 'Bridgetown, Barbados', '1st', '5 km', '21:24.33 CR'], ['2004', 'Central American and Caribbean Junior Championships (U-20)', 'Coatzacoalcos, México', '1st', '10 km', '43:21.99'], ['2004', 'World Junior Championships', 'Grosseto, Italy', '4th', '10 km', '41:01.64'], ['2005', 'World Championships', 'Helsinki, Finland', '8th', '20 km', '1:20:45'], ['2006', 'Central American and Caribbean Games', 'Cartagena, Colombia', '2nd', '20\xa0km', '1:26:30'], ['2007', 'World Championships', 'Osaka, Japan', '4th', '20 km', '1:23:36'], ['2008', 'Olympic Games', 'Beijing, PR China', '15th', '20 km', '1:21:53'], ['2009', 'World Championships', 'Berlin, Germany', '3rd', '20 km', '1:19:22'], ['2010', 'Central American and Caribbean Games', 'Mayagüez, Puerto Rico', '1st', '20 km', '1:22:32 GR'], ['2011', 'World Championships', 'Daegu, Korea', '15th', '20 km', '1:23:05'], ['2011', 'Pan American Games', 'Guadalajara, Mexico', '6th', '20 km', '1:25:00']],
    "question": "where was the only 5km event held?",
    "answer": "Bridgetown, Barbados",
    "step_1": "The only 5km event (identified from cell (0,5)) was held in Bridgetown, Barbados (identified from cell (0,3)).",
    "step_2": "5km (0,5), Bridgetown, Barbados (0,3)",
    "step_3": "5km (0,5)",
    "step_4": "Bridgetown, Barbados (0,3)",
    "step_5": "(0,5), (0,3)"
}

EXAMPLE_4 = {
    "table_array": [["Year", "Team", "Games", "Combined Tackles", "Tackles", "Assisted Tackles", "Sacks", "Forced Fumbles", "Fumble Recoveries", "Fumble Return Yards", "Interceptions", "Interception Return Yards", "Yards per Interception Return", "Longest Interception REturn", "Interceptions Returned for Touchdown", "Passes Defended"], ["2002", "BUF", "16", "96", "71", "25", "3.0", "0", "0", "0", "0", "0", "0", "0", "0", "1"], ["2003", "BUF", "16", "28", "24", "4", "1.0", "0", "0", "0", "0", "0", "0", "0", "0", "2"], ["2004", "BUF", "12", "25", "14", "11", "1.0", "0", "1", "0", "0", "0", "0", "0", "0", "0"], ["2005", "BUF", "13", "9", "6", "3", "0.0", "1", "0", "0", "0", "0", "0", "0", "0", "0"], ["2006", "BUF", "16", "23", "13", "10", "0.0", "0", "0", "0", "0", "0", "0", "0", "0", "0"], ["2007", "BUF", "7", "4", "3", "1", "0.0", "0", "0", "0", "0", "0", "0", "0", "0", "0"], ["2008", "ATL", "16", "34", "28", "6", "0.0", "0", "0", "0", "0", "0", "0", "0", "0", "1"], ["2009", "ATL", "16", "17", "15", "2", "0.0", "1", "2", "0", "0", "0", "0", "0", "0", "1"], ["2010", "ATL", "15", "12", "8", "4", "0.0", "0", "1", "0", "0", "0", "0", "0", "0", "0"], ["Career", "", "127", "248", "182", "66", "5.0", "2", "4", "0", "0", "0", "0", "0", "0", "5"]],
    "question": "for which team did this player have the least amount of games played?",
    "answer": "BUF",
    "step_1": """To find the team for which this player have the least amount of games played, we must look at all  the entires in the Team and Games Column: 
    BUF (identified from cell (0,2)) played 16 games (identified from cell (0,3))
    BUF (identified from cell (1,2)) played 16 games (identified from cell (1,3))
    BUF (identified from cell (2,2)) played 12 games (identified from cell (2,3))
    BUF (identified from cell (3,2)) played 13 games (identified from cell (3,3))
    BUF (identified from cell (4,2)) played 16 games (identified from cell (4,3))
    BUF (identified from cell (5,2)) played 7 games (identified from cell (5,3))
    ATL (identified from cell (6,2)) played 16 games (identified from cell (6,3))
    ATL (identified from cell (7,2)) played 16 games (identified from cell (7,3))
    ATL (identified from cell (8,2)) played 15 games (identified from cell (8,3))
    
    Thus, the team for which this player have the least amount of games played is BUF with 7 games.""",
    "step_2": "BUF (0,2), 16 (0,3), BUF (1,2), 16 (1,3), BUF (2,2), 12 (2,3), BUF (3,2), 13 (3,3), BUF (4,2), 16 (4,3), BUF (5,2), 7 (5,3), ATL (6,2), 16 (6,3), ATL (7,2), 16 (7,3), ATL (8,2), 15 (8,3)",
    "step_3": "None",
    "step_4": "BUF (0,2), BUF (1,2), BUF (2,2), BUF (3,2), BUF (4,2), BUF (5,2)",
    "step_5": "(0,2), (0,3), (1,2), (1,3), (2,2), (2,3), (3,2), (3,3), (4,2), (4,3), (5,2), (5,3), (6,2), (6,3), (7,2), (7,3), (8,2), (8,3)"
}

PROMPT_TEMPLATE = """You are given a table, alongside a question based on the table and its answer, your task is to identify and report the specific cells within the table that directly provide the answer or were indirectly used to derive the answer. This task may require you to examine each cell attentively, as the necessary evidence could be found across various rows and columns. The identification process might involve mathematical calculations (such as addition, subtraction, or counting) or logical deductions based on information spread across multiple table entries. Each row in the table is given in a new line, and different columns are separated by a ' | ' symbol. Indices of the rows and columns are also specified to aid in answering the query.

The reason should include the cell indices of every reference, even name-lookup from the table of entities in the question and the entity in the final answer. If the evidence is spread across multiple rows or columns, ensure all relevant cells are listed. If no relevant evidence can be located within the table to support the answer, you should respond with 'None'. If the final answer is inferred from a cell, that cell's indices should also be included in the evidence. Thus, the evidence cells are union of question cells, final answer cells and all the cells used for reasoning to get to the answer cell(s) from the question cell(s).

Your response should format the evidence as follows: "Evidence cells: (Row1, Column1), (Row2, Column2), (Row3, Column3)", adjusting as needed for multiple entries. 

IMPORTANT: To identify the evidence cells, you must follow the following steps:
Step 1: Carefully analyze the table, the question and the answer provided and write a detailed reason behind getting the answer given the question and the table. Make it as explicit as possible, and include all the cell references from the table individually which were used to derive the answer or were directly used to provide the answer. IMPORTANT: YOU MUST MAKE THIS AS EXPLICIT AND DETAILED AS POSSIBLE, MENTIONING NOT JUST THE APPROACH BUT WHAT OPERATIONS WERE PERFORMED ON WHAT CELLS TO REACH THE ANSWER. DO NOT JUST MENTION THE COLUMN NAMES THAT WERE USED IN ARRIVING AT THE ANSWER, BUT MENTION INDIVIDUAL CELLS AS (row, column) THAT WERE USED IN THE REASONING. DO NOT INCLUDE OTHER CELLS OF THE SAME ROW THAT AREN'T USED IN THE REASONING.
Step 2: From the reason and the table, list out all the references from the table in the intermediate reasoning along with their respective cell locations. ENSURE that any information mentioned in the reason that is also present in the table is included here with the cell location. IMPORTANT: Any information that is used in the reason that is present in the table should be included here. DO NOT LEAVE ANY INFORMATION. IMPORTANT: YOU MUST LIST EACH REFERENCE EXPLICITLY AND MENTION THE CELL LOCATION. DO NOT INCLUDE OTHER CELLS OF THE SAME ROW THAT AREN'T USED IN THE REASONING. DO NOT LEAVE OUT THE CELL INDICES.
Step 3: List out all the references to the cells of the table that were mentioned in the question. IMPORTANT: YOU MUST LIST EACH REFERENCE IN THE QUESTION TO A TABLE CELL EXPLICITLY AND MENTION THE CELL LOCATION. DO NOT INCLUDE OTHER CELLS OF THE SAME ROW THAT AREN'T USED IN THE QUESTION. IT IS OF UTMOST IMPORTANCE THAT THE CELL LOCATION BE MENTIONED. DO NOT LEAVE OUT THE CELL INDICES.
Step 4: List out all the references to the cells of the table that were mentioned in the answer. IMPORTANT: YOU MUST LIST EACH REFERENCE IN THE ANSWER TO A TABLE CELL EXPLICITLY AND MENTION THE CELL LOCATION. DO NOT INCLUDE OTHER CELLS OF THE SAME ROW THAT AREN'T USED IN THE ANSWER. IT IS OF UTMOST IMPORTANCE THAT THE CELL LOCATION BE MENTIONED. DO NOT LEAVE OUT THE CELL INDICES.
Step 5: Combine all the cell references identified in step 2, 3 and 4, list out all these cells from the table here. IMPORTANT YOU MUST INCLUDE EVERY REFERENCE IDENTIFIED FROM STEP 2, 3 AND 4 HERE.

Here are a few examples, with index columns added separately for clarity in the table. The index column is also considered while finding the cell indices:

Example 1
Table:  
{ex1_table}

Question: {ex1_question}
Answer: {ex1_answer}
Step 1 Reason: {ex1_step_1}
Step 2 References to table in the reason: {ex1_step_2}
Step 3 References to table in the question: {ex1_step_3}
Step 4 References to table in the answer: {ex1_step_4}
Step 5 Evidence cells: {ex1_step_5}

Example 2
Table:
{ex2_table}

Question: {ex2_question}
Answer: {ex2_answer}
Step 1 Reason: {ex2_step_1}
Step 2 References to table in the reason: {ex2_step_2}
Step 3 References to table in the question: {ex2_step_3}
Step 4 References to table in the answer: {ex2_step_4}
Step 5 Evidence: {ex2_step_5}

Example 3
Table:
{ex3_table}

Question: {ex3_question}
Answer: {ex3_answer}
Step 1 Reason: {ex3_step_1}
Step 2 References to table in the reason: {ex3_step_2}
Step 3 References to table in the question: {ex3_step_3}
Step 4 References to table in the answer: {ex3_step_4}
Step 5 Evidence: {ex3_step_5}

Example 4
Table:
{ex4_table}

Question: {ex4_question}
Answer: {ex4_answer}
Step 1 Reason: {ex4_step_1}
Step 2 References to table in the reason: {ex4_step_2}
Step 3 References to table in the question: {ex4_step_3}
Step 4 References to table in the answer: {ex4_step_4}
Step 5 Evidence: {ex4_step_5}

Now, given the table, question and answer, you need to identify the evidence cells while following step 1, step 2 and step 3. Do not include extra information. You must follow the following steps as illustrated above. IMPORTANT: FOLLOW THE DETAIL AND THE PATTERN FOR EACH STEP THAT HAS BEEN DESCRIBED ABOVE. PERFORM ALL THE FIVE STEPS IN THE ORDER THAT IS DESCRIBED ABOVE. REMEMBER THAT THE FIRST ROW SPECIFIES THE HEADERS OF THE TABLE AND THUS DOESN'T COUNT TOWARDS THE INDICES.

Table:
{table_string}
Question: {question}
Answer: {answer}
Step 1 Reason: """

In [66]:
# PROMPT_TEMPLATE = """You are given a table, alongside a question based on the table and its answer, your task is to identify and report the specific cells within the table that directly provide the answer or were indirectly used to derive the answer.This task may require you to examine each cell attentively, as the necessary evidence could be found across various rows and columns. The identification process might involve mathematical calculations (such as addition, subtraction, or counting) or logical deductions based on information spread across multiple table entries. Each row in the table is given in a new line, and different columns are separated by a tab space. Indices of the rows and columns are also specified to aid in answering the query.
# The reason should the cell indices of every reference, even name-lookup from the table.  If the evidence is spread across multiple rows or columns, ensure all relevant locations are listed. If no relevant evidence can be located within the table to support the answer, you should respond with 'None'. If the final answer is inferred from a cell, that cell's indices should also be included in the evidence. So now the evidence cells are union of final answers and all the cells used to get to reason.
# Note that if no relevant evidence can be located within the table to support the answer, you should respond with 'None'. Conversely, if appropriate evidence is found, please indicate it by specifying the row and column numbers. For cases requiring information from multiple rows or columns, ensure all relevant locations are listed.
# For example, if "William McCreery" is mentioned in the cells (0,1) and (0,2), and "March 4, 1803" is mentioned in the cell (0,3), then the reason should include all these cells.
# Your response should format the evidence as follows: "Evidence cells: (Row1, Column1), (Row2, Column2), (Row3, Column3)", adjusting as needed for multiple entries. Below are examples to illustrate how to approach different types of questions and answers:

# Here are a few examples, with index columns added separately for clarity in the table (and not counted in the cell indices):
# Table:  
#     0                   1         2      3
# index  Team                County    Wins   Years won 
# 0  Greystones          Wicklow       1        2011
# 1  Ballymore Eustace   Kildare       1        2010
# 2  Maynooth            Kildare       1        2009
# 3  Ballyroan Abbey     Laois         1        2008
# 4  Fingal Ravens       Dublin        1        2007
# 5  Confey              Kildare       1        2006
# 6  Crettyard           Laois         1        2005
# 7  Wolfe Tones         Meath         1        2004
# 8  Dundalk Gaels       Louth         1        2003

# Question: which team won previous to crettyard?
# Answer: Wolfe Tones
# Reason: crettyard (identified from cell (6,0)) won in 2005 (identified from cell (6,4)), so the previous team would have won in 2004 (identified from cell (7,4)) which is Wolfe Tones (identified from cell (7,0)).
# Evidence cells: (6,0), (6,4), (7,4), (7,0)

# Table:
#     0    1                    2                   3                4                       5
# index       Name                 Took office         Left office      Party                   Notes/Events                                                      
# 0   11  William McCreery     March 4, 1803       March 3, 1809    Democratic Republican                                                                     
# 1   12  Alexander McKim      March 4, 1809       March 3, 1815    Democratic Republican                                                                     
# 2   13  William Pinkney      March 4, 1815       April 18, 1816   Democratic Republican   Resigned to accept position as Minister Plenipotentiary to Russia 
# 3   14  Peter Little         September 2, 1816   March 3, 1823    Democratic Republican                                                                     
# 4   14  Peter Little         March 4, 1823       March 3, 1825    Jacksonian DR                                                                             
# 5   14  Peter Little         March 4, 1825       March 3, 1829    Adams                                                                                     
# 6   15  Benjamin C. Howard   March 4, 1829       March 3, 1833    Jacksonian   
# Question : how many people stayed at least 3 years in office?
# Answer : 4
# Reason: Take the difference between all the cells (0, 2), (0,3) & (1,2), (1,3) & (2,2), (2,3) & (3,2), (3,3) & (5,2), (5,3) & (6,2), (6,3) and count the number of differences greater than 3. We will find only the difference in the rows 0, 1, 5 and 6 is greater than 3. Thus, the answer is 4.
# Evidence : (0,2), (0,3), (1,2), (1,3), (2,2), (2,3), (3,2), (3,3), (5,2), (5,3), (6,2), (6,3)

# Now, given the table, question and answer, you need to identify the evidence cells and provide the reason and evidence cells based upon the question, answer and the reason identified in the format mentioned above. IMPORTANT: Only mention the reason and evidence cells as described in the format above. Do not include extra information. T
# Table:
# {table_string}
# Question: {question}
# Answer: {answer}
# Reason: """

In [67]:
quesid_to_prompts = {}

for question_id in remaining_ques_ids:
    table_array = tables_dict[questions_dict[question_id]["table_context"]]['original_table_array']
    table_string = generate_table_string(table_array)
    
    current_prompt = PROMPT_TEMPLATE.format(table_string=table_string, question=questions_dict[question_id]["question"], answer=questions_dict[question_id]["answer"], ex1_table=generate_table_string(EXAMPLE_1["table_array"]), ex1_question=EXAMPLE_1["question"], ex1_answer=EXAMPLE_1["answer"], ex1_step_1=EXAMPLE_1["step_1"], ex1_step_2=EXAMPLE_1["step_2"], ex1_step_3=EXAMPLE_1["step_3"], ex1_step_4=EXAMPLE_1["step_4"], ex1_step_5=EXAMPLE_1["step_5"], ex2_table=generate_table_string(EXAMPLE_2["table_array"]), ex2_question=EXAMPLE_2["question"], ex2_answer=EXAMPLE_2["answer"], ex2_step_1=EXAMPLE_2["step_1"], ex2_step_2=EXAMPLE_2["step_2"], ex2_step_3=EXAMPLE_2["step_3"], ex2_step_4=EXAMPLE_2["step_4"], ex2_step_5=EXAMPLE_2["step_5"], ex3_table=generate_table_string(EXAMPLE_3["table_array"]), ex3_question=EXAMPLE_3["question"], ex3_answer=EXAMPLE_3["answer"], ex3_step_1=EXAMPLE_3["step_1"], ex3_step_2=EXAMPLE_3["step_2"], ex3_step_3=EXAMPLE_3["step_3"], ex3_step_4=EXAMPLE_3["step_4"], ex3_step_5=EXAMPLE_3["step_5"], ex4_table=generate_table_string(EXAMPLE_4["table_array"]), ex4_question=EXAMPLE_4["question"], ex4_answer=EXAMPLE_4["answer"], ex4_step_1=EXAMPLE_4["step_1"], ex4_step_2=EXAMPLE_4["step_2"], ex4_step_3=EXAMPLE_4["step_3"], ex4_step_4=EXAMPLE_4["step_4"], ex4_step_5=EXAMPLE_4["step_5"])

    quesid_to_prompts[question_id] = current_prompt

with open("/home/suyash/final_repo/WikiTableQuestions/src/evidence_extraction/implicit_questions_prompt.json", "w") as f:
    json.dump(quesid_to_prompts, f)

KeyError: 'answer'

In [ ]:
# ### Estimating cost/number of tokens
# from transformers import GPT2Tokenizer

# def estimate_tokens(text):
#     tokenizer = GPT2Tokenizer.from_pretrained('gpt2')
#     tokens = tokenizer.encode(text)
#     return len(tokens)

# # Example usage
# total_tokens = 0
# for ques_id, prompt in quesid_to_prompts.items():
#     total_tokens += estimate_tokens(prompt)

# print(total_tokens)

In [ ]:
import random
# Select first 100 questions
# pruned_keys = ["nt-99","nt-100","nt-101","nt-102","nt-103","nt-104","nt-105","nt-106","nt-107","nt-108"]
all_keys = list(quesid_to_prompts.keys())
pruned_keys = random.sample(all_keys, 15)
small_queries = {k: quesid_to_prompts[k] for k in pruned_keys}
with open("/home/suyash/final_repo/WikiTableQuestions/src/evidence_extraction/gpt3_5_smal.json", "w") as f:
    json.dump(small_queries, f, indent=4)

In [ ]:
def get_completion(query):
    return ""

In [ ]:
import json

with open("gpt3_5_smal.json") as f:
    queries = json.load(f)

outputs = {}
for qid, query in queries.items():
    output = get_completion(query)
    outputs[qid] = output

with open("small_outputs.json", "w") as f:
    json.dump(outputs, f)

In [ ]:
for qid, output in outputs.items():
    prompt = queries[qid]
    idx = prompt.index("Only mention the reason and evidence cells as described in the format above. Do not include extra information") + 34
    prompt = prompt[idx:]
    print(prompt, end="")
    print(output)
